In [1]:
from orderbooklib import process_order_book_data 
import contextlib
from tqdm import tqdm
import matplotlib.pyplot as plt
#from modules.plotter2 import plot_bid_ask_curve
from orderbooklib  import process_order_book_data
#from modules.data_processor import DataProcessor, DataCleaner
import pandas as pd
import numpy as np
from D_processor import Data_Process,Data_Clean


In [2]:
df_ra = pd.read_csv("binance_incremental_book_L2_2022-01-23_BTCUSDT.csv.gz")
df_tr = pd.read_csv("binance_trades_2022-01-23_BTCUSDT.csv.gz")


In [ ]:
process = process_order_book_data(df_ra[:3990])
# process_l2 = Data_Process(df_tr,process)
# process_l3 = process_l2.merge_data_o_t()
# process_l5 = Data_Clean(process_l3)
# process_l6 = process_l5.fill_missing_trades()
#for _ ,row in process.iterrows():
#    order = row['order_book']
#    ask = order.get('ask',{})
#    print(ask.items())

In [7]:
print(process)

            timestamp                                         order_book
0    1642896002394650  {'bid': {35073.57: 0.09482, 35073.11: 0.175, 3...
1    1642896002408000  {'bid': {35075.31: 0.16926, 35075.3: 0.13199, ...
2    1642896002508000  {'bid': {35075.31: 0.03983, 35075.3: 0.13199, ...
3    1642896002608000  {'bid': {35075.5: 0.0537, 35075.49: 0.175, 350...
4    1642896002708000  {'bid': {35077.56: 0.21, 35075.94: 0.175, 3507...
..                ...                                                ...
164  1642896018916000  {'bid': {35079.36: 0.08263, 35079.28: 0.175, 3...
165  1642896019016000  {'bid': {35079.36: 0.08263, 35079.28: 0.175, 3...
166  1642896019116000  {'bid': {35079.36: 0.08263, 35079.28: 0.175, 3...
167  1642896019216000  {'bid': {35079.36: 0.08263, 35079.28: 0.175, 3...
168  1642896019316000  {'bid': {35079.36: 0.08263, 35079.28: 0.175, 3...

[169 rows x 2 columns]


In [4]:
# def calculate_ob_imbalance(order_book):
#     if not order_book['ask'] or not order_book['bid'] :
#         return None
#     bid_prices = list(order_book['bid'].keys())
#     ask_prices = list (order_book["ask"].keys())
#     max_bid_price = max(bid_prices)if bid_prices else 0
#     min_ask_price = min(ask_prices) if ask_prices else 0
#     mid_price   = (max_bid_price + min_ask_price) / 2

#     total_bid = 0
#     total_ask = 0

#     for price, qty in order_book["bid"].items():
#         if mid_price * 0.99 <= price <= mid_price*1.01:
#             total_bid += qty
#     for price, qty in order_book['ask'].items():
#         if mid_price*.99<= price <= mid_price*1.01:


#     imbalance = (total_bid - total_ask) / (total_bid + total_ask)

#     return imbalance , mid_price



In [4]:
def calculate_ob_imb(order_book):
    if not order_book['ask'] or not order_book['bid'] :
        return None
    mid_price = (max(order_book['bid'].keys())+ min(order_book['ask'].keys()))/2
    total_bid   = sum(qty for price, qty in order_book['bid'].items() if mid_price*.99<= price <= mid_price*1.01)
    total_ask   = sum(qty for price, qty in order_book['ask'].items() if mid_price*0.99 <= price <= mid_price*1.01)
    imbalance   = (total_bid - total_ask) / (total_bid + total_ask)
    return imbalance , mid_price 

In [6]:
def cal_zscore(df1, window_ = 20):
    col = ['imbalances']

    for cols in col :
        rolling_mean = df1[cols].rolling(window_ ).mean()
        rolling_st   = df1[cols].rolling(window_).std()
        zscore       = ( df1[cols] - rolling_mean )/ rolling_st
        df1['zscore'] = zscore
    return df1

In [ ]:
dfa = process[100:]
imbalance, mid_price = zip(*dfa['order_book'].apply(calculate_ob_imb))
dfa['imbalances'] = imbalance
dfa['mid_price']  = mid_price
dfa = dfa.set_index(pd.to_datetime(dfa['timestamp']/1000,unit = 'ms'))



In [ ]:
zscore = cal_zscore(dfa)
print(zscore['order_book'])
zscore[30:].zscore.plot()

In [9]:
df_minut = dfa[['imbalances','mid_price','zscore']].resample('10s').mean()

In [10]:
from oba import visual_data

In [11]:
visual_data(process,20)